In [ ]:
# use python 3.9 venv
# pip install tts

In [10]:
# pip install bangla==0.0.2

In [11]:
tts_config_path = "/home/bs-01483/Downloads/config.json"
checkpoint = "/home/bs-01483/Downloads/model_file.pth"

In [12]:
from TTS.config import load_config
from TTS.tts.models import setup_model

tts_config = load_config(tts_config_path)
model = setup_model(config=tts_config)

 > Using model: vits
 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024


In [13]:
model

Vits(
  (text_encoder): TextEncoder(
    (emb): Embedding(86, 192)
    (encoder): RelativePositionTransformer(
      (dropout): Dropout(p=0.1, inplace=False)
      (attn_layers): ModuleList(
        (0-5): 6 x RelativePositionMultiHeadAttention(
          (conv_q): Conv1d(192, 192, kernel_size=(1,), stride=(1,))
          (conv_k): Conv1d(192, 192, kernel_size=(1,), stride=(1,))
          (conv_v): Conv1d(192, 192, kernel_size=(1,), stride=(1,))
          (conv_o): Conv1d(192, 192, kernel_size=(1,), stride=(1,))
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
      (norm_layers_1): ModuleList(
        (0-5): 6 x LayerNorm2()
      )
      (ffn_layers): ModuleList(
        (0-5): 6 x FeedForwardNetwork(
          (conv_1): Conv1d(192, 768, kernel_size=(3,), stride=(1,))
          (conv_2): Conv1d(768, 192, kernel_size=(3,), stride=(1,))
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
      (norm_layers_2): ModuleList(
        (0-5): 6 x LayerNor

In [14]:
model.load_checkpoint(config= tts_config,checkpoint_path=checkpoint)
for param in model.parameters():
  print(param)

Parameter containing:
tensor([[ 0.0008, -0.0359, -0.0173,  ...,  0.0045,  0.0077,  0.0114],
        [-0.0175, -0.0130, -0.0265,  ...,  0.0401, -0.0544,  0.0206],
        [ 0.0057, -0.0125,  0.0373,  ...,  0.0381, -0.0375, -0.0293],
        ...,
        [ 0.0013,  0.0047,  0.0803,  ..., -0.0286, -0.0004, -0.0007],
        [ 0.1042, -0.0172,  0.0101,  ...,  0.0343,  0.0169,  0.0190],
        [ 0.0048, -0.0035,  0.0147,  ...,  0.0428,  0.0672, -0.0374]],
       requires_grad=True)
Parameter containing:
tensor([[[-6.8332e-01,  3.5352e-01, -5.1915e-01, -4.0042e-01, -5.5406e-01,
           7.5350e-02,  6.0412e-01,  4.5989e-01,  3.7652e-01,  1.4182e-01,
          -3.4793e-01, -9.2757e-02,  6.1467e-02,  5.3886e-01, -5.1551e-01,
           5.9900e-01,  7.4325e-01, -3.2198e-01,  4.1331e-01,  4.8168e-01,
           7.9612e-01,  4.1713e-01, -1.4472e-01,  4.6230e-01,  5.9122e-01,
          -4.8383e-01, -5.3891e-01,  5.5735e-01,  2.1208e-01, -1.6653e-01,
          -3.5363e-01,  2.3147e-01, -6.6243e-

In [ ]:
import os
import torch
import logging
import json
# Setup logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

def quantize_model(model, output_path):
    device = "cuda" if torch.cuda.is_available() else "cpu"

    os.makedirs(os.path.dirname(os.path.abspath(output_path)), exist_ok=True)

    # Apply dynamic quantization
    logger.info("Applying dynamic quantization...")
    quantized_model = torch.quantization.quantize_dynamic(
        model, {torch.nn.Linear, torch.nn.Conv1d, torch.nn.Conv2d}, dtype=torch.qint8
    )

    model_path = os.path.join(os.path.dirname(output_path), "model_file.pth")
    checkpoint = {
        "model": quantized_model.state_dict(),
        "version": getattr(quantized_model, "version", ""),
        "config": model.config.to_dict()
    }
    torch.save(checkpoint, model_path)

    config_path = os.path.join(os.path.dirname(output_path), "config.json")
    with open(config_path, 'w') as f:
        json.dump(model.config.to_dict(), f, indent=4)

    # Report size
    size_mb = os.path.getsize(model_path) / 1e6
    logger.info(f"Quantized model size: {size_mb:.2f} MB")

quantize_model(model, "./quants/")

INFO:__main__:Applying dynamic quantization...
INFO:__main__:Quantized model size: 332.60 MB
INFO:__main__:Quantization complete!
INFO:__main__:Quantized model size: 332.60 MB
INFO:__main__:Quantization complete!
